**By Huy Duc Vu - 25728181**

# Part 1: Data Ingestion and Preparation

##Load the data in separate df

In [0]:
path_green = f"/Volumes/workspace/bde/assignment2/green/"
path_yellow = f"/Volumes/workspace/bde/assignment2/yellow/"
path_lookup = f"/Volumes/workspace/bde/assignment2/"

df_green = spark.read.option("header", True).parquet(path_green)
df_yellow = spark.read.option("header", True).parquet(path_yellow)
df_lookup = spark.read.option("header", True).csv(path_lookup)

## 1.4. Explore dataset

In [0]:
df_green.printSchema()
print(f"Record count: ", df_green.count())

root
 |-- VendorID: long (nullable = true)
 |-- lpep_pickup_datetime: timestamp (nullable = true)
 |-- lpep_dropoff_datetime: timestamp (nullable = true)
 |-- store_and_fwd_flag: string (nullable = true)
 |-- RatecodeID: double (nullable = true)
 |-- PULocationID: long (nullable = true)
 |-- DOLocationID: long (nullable = true)
 |-- passenger_count: double (nullable = true)
 |-- trip_distance: double (nullable = true)
 |-- fare_amount: double (nullable = true)
 |-- extra: double (nullable = true)
 |-- mta_tax: double (nullable = true)
 |-- tip_amount: double (nullable = true)
 |-- tolls_amount: double (nullable = true)
 |-- ehail_fee: double (nullable = true)
 |-- improvement_surcharge: double (nullable = true)
 |-- total_amount: double (nullable = true)
 |-- payment_type: double (nullable = true)
 |-- trip_type: double (nullable = true)
 |-- congestion_surcharge: double (nullable = true)

Record count:  83484688


In [0]:
df_yellow.printSchema()
print(f"Record count: ", df_yellow.count())

root
 |-- VendorID: long (nullable = true)
 |-- tpep_pickup_datetime: timestamp (nullable = true)
 |-- tpep_dropoff_datetime: timestamp (nullable = true)
 |-- passenger_count: double (nullable = true)
 |-- trip_distance: double (nullable = true)
 |-- RatecodeID: double (nullable = true)
 |-- store_and_fwd_flag: string (nullable = true)
 |-- PULocationID: long (nullable = true)
 |-- DOLocationID: long (nullable = true)
 |-- payment_type: long (nullable = true)
 |-- fare_amount: double (nullable = true)
 |-- extra: double (nullable = true)
 |-- mta_tax: double (nullable = true)
 |-- tip_amount: double (nullable = true)
 |-- tolls_amount: double (nullable = true)
 |-- improvement_surcharge: double (nullable = true)
 |-- total_amount: double (nullable = true)
 |-- congestion_surcharge: double (nullable = true)
 |-- airport_fee: double (nullable = true)

Record count:  907982776


In [0]:
df_lookup.printSchema()

root
 |-- LocationID: string (nullable = true)
 |-- Borough: string (nullable = true)
 |-- Zone: string (nullable = true)
 |-- service_zone: string (nullable = true)



In [0]:
df_green.createOrReplaceTempView("df_green")

In [0]:
df_yellow.createOrReplaceTempView("df_yellow")

In [0]:
df_lookup.createOrReplaceTempView("df_lookup")

### 1.4.1. Explore and clean green taxi records

In [0]:
%sql
--sample data
SELECT * 
FROM df_green
LIMIT(10)

VendorID lpep_pickup_datetime lpep_dropoff_datetime store_and_fwd_flag RatecodeID PULocationID DOLocationID passenger_count trip_distance fare_amount extra mta_tax tip_amount tolls_amount ehail_fee improvement_surcharge total_amount payment_type trip_type congestion_surcharge 2 2014-01-01T00:17:26.000Z 2014-01-01T00:37:11.000Z N 1.0 17 225 1.0 2.28 13.5 0.5 0.5 0.0 0.0 null null 14.5 2.0 null null 1 2014-01-01T00:29:12.000Z 2014-01-01T00:37:43.000Z N 1.0 127 241 1.0 2.1 9.0 0.0 0.5 0.0 0.0 null null 9.5 2.0 null null 2 2014-01-01T00:31:35.000Z 2014-01-01T00:44:09.000Z N 1.0 166 243 1.0 4.72 15.5 0.5 0.5 4.0 0.0 null null 20.5 1.0 null null 2 2014-01-01T00:07:01.000Z 2014-01-01T00:21:54.000Z N 1.0 7 157 1.0 2.88 13.0 0.5 0.5 2.88 0.0 null null 16.88 1.0 null null 2 2014-01-01T00:26:43.000Z 2014-01-01T00:37:17.000Z N 1.0 83 197 2.0 3.8 13.0 0.5 0.5 0.0 0.0 null null 14.0 2.0 null null 2 2014-01-01T00:23:34.000Z 2014-01-01T00:32:50.000Z N 1.0 226 7 6.0 1.85 9.0 0.5 0.5 2.85 0.0 null null 12.85 1.0 null null 2 2014-01-01T00:45:12.000Z 2014-01-01T00:54:03.000Z N 1.0 7 95 6.0 7.01 20.0 0.5 0.5 4.1 0.0 null null 25.1 1.0 null null 2 2014-01-01T00:10:17.000Z 2014-01-01T00:48:42.000Z N 1.0 61 74 2.0 13.91 42.5 0.5 0.5 8.6 0.0 null null 52.1 1.0 null null 2 2014-01-01T00:53:39.000Z 2014-01-01T01:05:19.000Z N 1.0 74 116 2.0 2.0 10.0 0.5 0.5 2.1 0.0 null null 13.1 1.0 null null 2 2014-01-01T00:15:50.000Z 2014-01-01T00:20:59.000Z N 1.0 61 83 2.0 1.28 6.5 0.5 0.5 0.0 0.0 null null 7.5 2.0 null null

In [0]:
%sql
--record count
SELECT COUNT(*) AS record_count
FROM df_green

record_count 83484688

In [0]:
%sql
--pickup/dropoff time
SELECT COUNT(*) AS invalid_1
FROM df_green
WHERE lpep_pickup_datetime > lpep_dropoff_datetime OR lpep_pickup_datetime = lpep_dropoff_datetime

invalid_1 68318

In [0]:
%sql 
--pickup/dropoff time
SELECT MAX(lpep_pickup_datetime) as max_pickup_datetime,
      MIN(lpep_pickup_datetime) as min_pickup_datetime,
      MAX(lpep_dropoff_datetime) as max_dropoff_datetime,
      MIN(lpep_dropoff_datetime) as min_dropoff_datetime
FROM df_green

max_pickup_datetime min_pickup_datetime max_dropoff_datetime min_dropoff_datetime 2081-06-24T17:40:37.000Z 2008-10-21T15:52:05.000Z 2081-06-24T18:42:47.000Z 2008-10-21T15:54:26.000Z

In [0]:
%sql 
--pickup/dropoff time
SELECT COUNT(*) as invalid_2
FROM df_green
WHERE (DATE(lpep_pickup_datetime) < DATE('2013-08-01') OR DATE(lpep_pickup_datetime) > DATE('2024-12-31')) 
  OR (DATE(lpep_dropoff_datetime) < DATE('2013-08-01') OR DATE(lpep_dropoff_datetime) > DATE('2024-12-31'))

invalid_2 816

In [0]:
%sql
--speed
SELECT COUNT(*) as invalid_3
FROM df_green
WHERE lpep_dropoff_datetime != lpep_pickup_datetime AND ((trip_distance / ((unix_timestamp(lpep_dropoff_datetime) - unix_timestamp(lpep_pickup_datetime))/3600)) < 1
                                        OR (trip_distance / ((unix_timestamp(lpep_dropoff_datetime) - unix_timestamp(lpep_pickup_datetime))/3600)) > 70 )

invalid_3 1954124

In [0]:
%sql
--passenger
SELECT passenger_count, COUNT(*)
FROM df_green
GROUP BY passenger_count
ORDER BY passenger_count DESC

passenger_count COUNT(*) 48.0 1 32.0 1 9.0 615 8.0 2071 7.0 1854 6.0 1344714 5.0 3068841 4.0 531213 3.0 1668535 2.0 6221946 1.0 68698946 0.0 60805 null 1885146

In [0]:
%sql
--distance
SELECT MAX(trip_distance), MIN(trip_distance), ROUND(AVG(trip_distance),2)
FROM df_green

MAX(trip_distance) MIN(trip_distance) ROUND(AVG(trip_distance),2) 360068.14 -20329.08 6.18

In [0]:
%sql
--distance
SELECT COUNT(*)
FROM df_green
WHERE trip_distance > 100 OR trip_distance <= 0.2

COUNT(*) 2153559

In [0]:
%sql
--duration (min)
SELECT 
  MIN( (unix_timestamp(lpep_dropoff_datetime) - unix_timestamp(lpep_pickup_datetime))/60 ) AS min_duration,
  MAX( (unix_timestamp(lpep_dropoff_datetime) - unix_timestamp(lpep_pickup_datetime))/60 ) AS max_duration,
  AVG( (unix_timestamp(lpep_dropoff_datetime) - unix_timestamp(lpep_pickup_datetime))/60 ) AS avg_duration
FROM df_green

min_duration max_duration avg_duration -525941.1833333333 3155397.5 19.332406346778217

In [0]:
%sql
--duration (min)
SELECT COUNT(*)
FROM df_green
WHERE ( (unix_timestamp(lpep_dropoff_datetime) - unix_timestamp(lpep_pickup_datetime))/60 ) < 1 OR
    ( (unix_timestamp(lpep_dropoff_datetime) - unix_timestamp(lpep_pickup_datetime))/60 ) > 120

COUNT(*) 1863205

In [0]:
%sql
SELECT DISTINCT(PULocationID) FROM df_green
EXCEPT
SELECT LocationID FROM df_lookup;

PULocationID

In [0]:
%sql
SELECT DISTINCT(DOLocationID) FROM df_green
EXCEPT
SELECT LocationID FROM df_lookup;

DOLocationID

In [0]:
%sql
SELECT RatecodeID, COUNT(*) 
FROM df_green
GROUP BY RatecodeID
ORDER BY RatecodeID DESC;


RatecodeID COUNT(*) 99.0 943 6.0 1822 5.0 1998838 4.0 47204 3.0 56142 2.0 222391 1.0 79272202 null 1885146

In [0]:
%sql
SELECT payment_type, COUNT(*)
FROM df_green
GROUP BY payment_type
ORDER BY payment_type;


payment_type COUNT(*) null 1885146 1.0 40139353 2.0 40916360 3.0 325132 4.0 215340 5.0 3357

In [0]:
%sql
SELECT store_and_fwd_flag, COUNT(*)
FROM df_green
GROUP BY store_and_fwd_flag;


store_and_fwd_flag COUNT(*) Y 391751 N 81207791 null 1885146

In [0]:
%sql
SELECT trip_type, COUNT(*)
FROM df_green
GROUP BY trip_type;


trip_type COUNT(*) null 3667901 1.0 77908169 2.0 1908618

In [0]:
%sql
SELECT VendorID, COUNT(*)
FROM df_green
GROUP BY VendorID;

VendorID COUNT(*) 2 67112174 1 16372267 5 47 6 200

In [0]:
%sql
SELECT MAX(total_amount), MIN(total_amount)
FROM df_green

MAX(total_amount) MIN(total_amount) 989970.39 -890.3

In [0]:
%sql
--total amount
SELECT COUNT(*)
FROM df_green
WHERE total_amount <= 0 OR total_amount > 500

COUNT(*) 368053

In [0]:
%sql
--total amount
SELECT COUNT(*)
FROM df_green
WHERE total_amount <= 0 AND payment_type = 6

COUNT(*) 0

In [0]:
%sql 

CREATE OR REPLACE TEMPORARY VIEW df_green_cleaned AS
WITH 
p AS (
  SELECT
    TIMESTAMP('2013-08-01 00:00:00') AS min_date,
    TIMESTAMP('2024-12-31 23:59:59') AS max_date,
    1.0 AS min_speed,
    70.0 AS max_speed,
    1.0 AS min_duration,
    120.0 AS max_duration,
    0.2 AS min_distance,
    100.0 AS max_distance,
    5 AS passenger_cap
),

base AS (
  SELECT 
    'green' AS color,
    VendorID AS VendorID_raw,
    lpep_pickup_datetime AS pickup_dt,
    lpep_dropoff_datetime AS dropoff_dt,
    store_and_fwd_flag AS store_and_fwd_flag,
    CAST(trip_distance AS double) AS trip_distance,
    CAST(passenger_count AS int) AS passenger_raw,
    
    RatecodeID AS RatecodeID_raw,
    PULocationID AS PULocationID,
    DOLocationID AS DOLocationID,
    fare_amount AS fare_amount,
    extra AS extra,
    mta_tax AS mta_tax,
    tip_amount AS tip_amount,
    tolls_amount AS tolls_amount,
    improvement_surcharge AS improvement_surcharge,
    congestion_surcharge AS congestion_surcharge,
    ehail_fee AS ehail_fee,
    CAST(total_amount AS double) AS total_amount,
    CAST(payment_type AS int) AS payment_type_raw,
    trip_type AS trip_type
  FROM df_green
),

derived AS(
  SELECT * EXCEPT (passenger_raw, RatecodeID_raw, VendorID_raw, payment_type_raw),
    (unix_timestamp(dropoff_dt) - unix_timestamp(pickup_dt))/60 AS trip_duration_min,
    (unix_timestamp(dropoff_dt) - unix_timestamp(pickup_dt))/3600 AS trip_duration_hr,
    CASE 
      WHEN passenger_raw IS NULL THEN NULL
      WHEN passenger_raw < 0 THEN NULL
      WHEN passenger_raw = 0 THEN 1
      WHEN passenger_raw > (SELECT passenger_cap FROM p) THEN (SELECT passenger_cap FROM p)
      ELSE passenger_raw
    END AS passenger_count,
    CASE
      WHEN RatecodeID_raw IS NULL THEN 99
      ELSE RatecodeID_raw
    END AS RatecodeID,
    CASE
      WHEN VendorID_raw = 5 THEN 6
      ELSE VendorID_raw
    END AS VendorID,
    CASE
      WHEN payment_type_raw IS NULL THEN 5
      ELSE payment_type_raw
    END AS payment_type
  FROM base
)

SELECT * EXCEPT (trip_duration_min, trip_duration_hr)
FROM derived
WHERE 
  dropoff_dt > pickup_dt
  AND pickup_dt BETWEEN (SELECT min_date FROM p) AND (SELECT max_date FROM p)
  AND dropoff_dt BETWEEN (SELECT min_date FROM p) AND (SELECT max_date FROM p)

  AND trip_duration_min BETWEEN (SELECT min_duration FROM p) AND (SELECT max_duration FROM p)
  
  AND trip_distance <= (SELECT max_distance FROM p)
  AND trip_distance > (SELECT min_distance FROM p)

  AND (trip_distance/ NULLIF(trip_duration_hr,0) ) BETWEEN (SELECT min_speed FROM p) AND (SELECT max_speed FROM p)

  AND total_amount IS NOT NULL
  AND total_amount > 0 
  AND total_amount <= 200

  AND PULocationID IS NOT NULL
  AND DOLocationID IS NOT NULL
;

In [0]:
%sql
--Count of green records before and after cleaned, cleaned ratio
SELECT 
  raw_count,
  cleaned_count,
  cleaned_count / raw_count AS ratio
FROM (
  SELECT 
    (SELECT COUNT(*) FROM df_green) AS raw_count,
    (SELECT COUNT(*) FROM df_green_cleaned) AS cleaned_count
)


raw_count cleaned_count ratio 83484688 80458710 0.9637540958409044

In [0]:
%sql
--Preview cleaned data
SELECT * FROM df_green_cleaned LIMIT 10

color pickup_dt dropoff_dt store_and_fwd_flag trip_distance PULocationID DOLocationID fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge congestion_surcharge ehail_fee total_amount trip_type passenger_count RatecodeID VendorID payment_type green 2014-01-01T00:17:26.000Z 2014-01-01T00:37:11.000Z N 2.28 17 225 13.5 0.5 0.5 0.0 0.0 null null null 14.5 null 1 1.0 2 2 green 2014-01-01T00:29:12.000Z 2014-01-01T00:37:43.000Z N 2.1 127 241 9.0 0.0 0.5 0.0 0.0 null null null 9.5 null 1 1.0 1 2 green 2014-01-01T00:31:35.000Z 2014-01-01T00:44:09.000Z N 4.72 166 243 15.5 0.5 0.5 4.0 0.0 null null null 20.5 null 1 1.0 2 1 green 2014-01-01T00:07:01.000Z 2014-01-01T00:21:54.000Z N 2.88 7 157 13.0 0.5 0.5 2.88 0.0 null null null 16.88 null 1 1.0 2 1 green 2014-01-01T00:26:43.000Z 2014-01-01T00:37:17.000Z N 3.8 83 197 13.0 0.5 0.5 0.0 0.0 null null null 14.0 null 2 1.0 2 2 green 2014-01-01T00:23:34.000Z 2014-01-01T00:32:50.000Z N 1.85 226 7 9.0 0.5 0.5 2.85 0.0 null null null 12.85 null 5 1.0 2 1 green 2014-01-01T00:45:12.000Z 2014-01-01T00:54:03.000Z N 7.01 7 95 20.0 0.5 0.5 4.1 0.0 null null null 25.1 null 5 1.0 2 1 green 2014-01-01T00:10:17.000Z 2014-01-01T00:48:42.000Z N 13.91 61 74 42.5 0.5 0.5 8.6 0.0 null null null 52.1 null 2 1.0 2 1 green 2014-01-01T00:53:39.000Z 2014-01-01T01:05:19.000Z N 2.0 74 116 10.0 0.5 0.5 2.1 0.0 null null null 13.1 null 2 1.0 2 1 green 2014-01-01T00:15:50.000Z 2014-01-01T00:20:59.000Z N 1.28 61 83 6.5 0.5 0.5 0.0 0.0 null null null 7.5 null 2 1.0 2 2

### 1.4.2. Explore and clean yellow taxi records

In [0]:
%sql
--sample data
SELECT * 
FROM df_yellow
LIMIT(10)

VendorID tpep_pickup_datetime tpep_dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge airport_fee 1 2015-01-01T00:11:33.000Z 2015-01-01T00:16:48.000Z 1.0 1.0 1.0 N 41 166 1 5.7 0.5 0.5 1.4 0.0 0.0 8.4 null null 1 2015-01-01T00:18:24.000Z 2015-01-01T00:24:20.000Z 1.0 0.9 1.0 N 166 238 3 6.0 0.5 0.5 0.0 0.0 0.0 7.3 null null 1 2015-01-01T00:26:19.000Z 2015-01-01T00:41:06.000Z 1.0 3.5 1.0 N 238 162 1 13.2 0.5 0.5 2.9 0.0 0.0 17.4 null null 1 2015-01-01T00:45:26.000Z 2015-01-01T00:53:20.000Z 1.0 2.1 1.0 N 162 263 1 8.2 0.5 0.5 2.37 0.0 0.0 11.87 null null 1 2015-01-01T00:59:21.000Z 2015-01-01T01:05:24.000Z 1.0 1.0 1.0 N 236 141 3 6.0 0.5 0.5 0.0 0.0 0.0 7.3 null null 1 2015-01-01T00:07:31.000Z 2015-01-01T00:11:32.000Z 1.0 0.8 1.0 N 239 238 2 5.0 0.5 0.5 0.0 0.0 0.0 6.3 null null 1 2015-01-01T00:47:08.000Z 2015-01-01T00:54:50.000Z 1.0 1.1 1.0 N 238 239 2 7.0 0.5 0.5 0.0 0.0 0.0 8.3 null null 1 2015-01-01T00:58:04.000Z 2015-01-01T01:11:56.000Z 1.0 2.9 1.0 N 238 42 1 12.2 0.5 0.5 2.7 0.0 0.0 16.2 null null 1 2015-01-01T00:29:25.000Z 2015-01-01T00:37:25.000Z 2.0 1.3 1.0 N 90 125 2 7.0 0.5 0.5 0.0 0.0 0.0 8.3 null null 1 2015-01-01T00:39:02.000Z 2015-01-01T01:02:37.000Z 2.0 4.3 1.0 N 125 141 2 18.0 0.5 0.5 0.0 0.0 0.0 19.3 null null

In [0]:
%sql
--record count
SELECT COUNT(*) AS record_count
FROM df_yellow

record_count 907982776

In [0]:
%sql
--pickup/dropoff time
SELECT COUNT(*) AS invalid_1
FROM df_yellow 
WHERE tpep_pickup_datetime > tpep_dropoff_datetime OR tpep_pickup_datetime = tpep_dropoff_datetime

invalid_1 1108986

In [0]:
%sql 
--pickup/dropoff time
SELECT MAX(tpep_pickup_datetime) as max_pickup_datetime,
      MIN(tpep_pickup_datetime) as min_pickup_datetime,
      MAX(tpep_dropoff_datetime) as max_dropoff_datetime,
      MIN(tpep_dropoff_datetime) as min_dropoff_datetime
FROM df_yellow

max_pickup_datetime min_pickup_datetime max_dropoff_datetime min_dropoff_datetime 2098-09-11T02:23:31.000Z 2001-01-01T00:01:48.000Z 2253-08-23T07:56:38.000Z 1900-01-01T00:00:00.000Z

In [0]:
%sql 
--pickup/dropoff time
SELECT COUNT(*) as invalid_2
FROM df_yellow
WHERE (DATE(tpep_pickup_datetime) < DATE('2009-01-01') OR DATE(tpep_pickup_datetime) > DATE('2024-12-31')) 
  OR (DATE(tpep_dropoff_datetime) < DATE('2009-01-01') OR DATE(tpep_dropoff_datetime) > DATE('2024-12-31'))

invalid_2 2030

In [0]:
%sql
--speed
SELECT COUNT(*) as invalid_3
FROM df_yellow
WHERE tpep_dropoff_datetime != tpep_pickup_datetime AND ((trip_distance / ((unix_timestamp(tpep_dropoff_datetime) - unix_timestamp(tpep_pickup_datetime))/3600)) < 1
                                        OR (trip_distance / ((unix_timestamp(tpep_dropoff_datetime) - unix_timestamp(tpep_pickup_datetime))/3600)) > 70 )

invalid_3 9576602

In [0]:
%sql
--passenger
SELECT passenger_count, COUNT(*)
FROM df_yellow
GROUP BY passenger_count
ORDER BY passenger_count DESC

passenger_count COUNT(*) 208.0 21 192.0 2 112.0 1 96.0 2 9.0 1560 8.0 2191 7.0 2403 6.0 25270727 5.0 39874337 4.0 18013034 3.0 37047055 2.0 130645897 1.0 641937657 0.0 5627509 null 9560380

In [0]:
%sql
--distance
SELECT MAX(trip_distance), MIN(trip_distance), ROUND(AVG(trip_distance),2)
FROM df_yellow

MAX(trip_distance) MIN(trip_distance) ROUND(AVG(trip_distance),2) 1.346190631E8 -4.08401244E7 6.95

In [0]:
%sql
--distance
SELECT COUNT(*)
FROM df_yellow
WHERE trip_distance > 100 OR trip_distance <= 0.2

COUNT(*) 13508639

In [0]:
%sql
--duration (min)
SELECT 
  MIN( (unix_timestamp(tpep_dropoff_datetime) - unix_timestamp(tpep_pickup_datetime))/60 ) AS min_duration,
  MAX( (unix_timestamp(tpep_dropoff_datetime) - unix_timestamp(tpep_pickup_datetime))/60 ) AS max_duration,
  AVG( (unix_timestamp(tpep_dropoff_datetime) - unix_timestamp(tpep_pickup_datetime))/60 ) AS avg_duration
FROM df_yellow

min_duration max_duration avg_duration -6.100172596666667E7 1.2537316083333333E8 18.22864841460017

In [0]:
%sql
--duration (min)
SELECT COUNT(*)
FROM df_yellow
WHERE ( (unix_timestamp(tpep_dropoff_datetime) - unix_timestamp(tpep_pickup_datetime))/60 ) < 1 OR
    ( (unix_timestamp(tpep_dropoff_datetime) - unix_timestamp(tpep_pickup_datetime))/60 ) > 120

COUNT(*) 9879433

In [0]:
%sql
SELECT DISTINCT(PULocationID) FROM df_yellow
EXCEPT
SELECT LocationID FROM df_lookup;

PULocationID

In [0]:
%sql
SELECT DISTINCT(DOLocationID) FROM df_yellow
EXCEPT
SELECT LocationID FROM df_lookup;

DOLocationID

In [0]:
%sql
SELECT RatecodeID, COUNT(*) 
FROM df_yellow
GROUP BY RatecodeID
ORDER BY RatecodeID DESC;


RatecodeID COUNT(*) 99.0 865174 6.0 8138 5.0 3738193 4.0 643545 3.0 1868503 2.0 21587774 1.0 869711069 null 9560380

In [0]:
%sql
SELECT payment_type, COUNT(*)
FROM df_yellow
GROUP BY payment_type
ORDER BY payment_type;

payment_type COUNT(*) 0 9560380 1 605369306 2 285770650 3 4063777 4 2735238 5 483425

In [0]:
%sql
SELECT store_and_fwd_flag, COUNT(*)
FROM df_yellow
GROUP BY store_and_fwd_flag;

store_and_fwd_flag COUNT(*) Y 7006626 N 841295532 null 59680618

In [0]:
%sql
SELECT VendorID, COUNT(*)
FROM df_yellow
GROUP BY VendorID;

VendorID COUNT(*) 2 527412701 1 379560281 3 10297 4 758881 5 1079 6 239307 7 230

In [0]:
%sql
SELECT * FROM df_yellow WHERE VendorID IN (3, 4, 5)

VendorID tpep_pickup_datetime tpep_dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge airport_fee 3 2016-05-02T07:33:07.000Z 2016-05-02T07:33:38.000Z 1.0 0.28 1.0 N 144 211 2 3.0 0.0 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-02T07:35:13.000Z 2016-05-02T07:35:34.000Z 1.0 0.1 1.0 N 211 211 2 2.5 0.0 0.5 1.0 0.0 0.3 4.3 null null 3 2016-05-02T07:54:31.000Z 2016-05-02T07:54:50.000Z 1.0 0.01 1.0 N 211 211 2 2.5 0.0 0.5 0.0 0.0 0.3 3.3 null null 3 2016-05-05T11:46:08.000Z 2016-05-05T11:46:13.000Z 1.0 0.0 1.0 N 207 207 2 2.5 0.0 0.5 0.0 0.0 0.3 3.3 null null 3 2016-05-05T11:51:00.000Z 2016-05-05T11:51:04.000Z 1.0 0.0 5.0 N 207 207 2 0.0 0.0 0.5 0.0 0.0 0.3 0.8 null null 3 2016-05-05T11:51:34.000Z 2016-05-05T11:51:42.000Z 1.0 0.0 5.0 N 207 207 2 0.0 0.0 0.5 0.09 5.54 0.3 6.43 null null 3 2016-05-05T11:52:46.000Z 2016-05-05T11:52:47.000Z 1.0 0.0 1.0 N 207 207 1 2.5 0.0 0.5 0.0 0.0 0.3 3.3 null null 3 2016-05-05T11:54:25.000Z 2016-05-05T11:54:26.000Z 1.0 0.0 5.0 N 207 207 2 0.0 0.0 0.5 0.0 0.0 0.3 0.8 null null 3 2016-05-05T11:55:03.000Z 2016-05-05T11:55:04.000Z 1.0 0.0 1.0 N 207 207 2 2.5 0.0 0.5 0.0 0.0 0.3 3.3 null null 3 2016-05-06T04:23:22.000Z 2016-05-06T04:23:23.000Z 1.0 0.0 1.0 N 207 207 2 2.5 0.5 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-06T04:23:36.000Z 2016-05-06T04:23:37.000Z 1.0 0.0 1.0 N 207 207 1 2.5 0.5 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-06T05:06:11.000Z 2016-05-06T05:06:17.000Z 1.0 0.0 1.0 N 207 207 1 2.5 0.5 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-06T05:17:07.000Z 2016-05-06T05:17:08.000Z 1.0 0.0 1.0 N 207 207 2 2.5 0.5 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-06T05:47:07.000Z 2016-05-06T05:47:08.000Z 1.0 0.0 1.0 N 207 207 2 2.5 0.5 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-06T05:55:28.000Z 2016-05-06T05:55:30.000Z 1.0 0.0 1.0 N 207 207 1 2.5 0.5 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-06T05:56:12.000Z 2016-05-06T05:56:13.000Z 1.0 0.0 1.0 N 207 207 1 2.5 0.5 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-06T05:57:32.000Z 2016-05-06T05:57:36.000Z 1.0 0.0 1.0 N 207 207 1 2.5 0.5 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-06T05:59:07.000Z 2016-05-06T05:59:17.000Z 1.0 0.0 1.0 N 207 207 1 2.5 0.5 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-06T06:11:30.000Z 2016-05-06T06:11:32.000Z 1.0 0.0 1.0 N 207 207 1 2.5 0.0 0.5 0.0 0.0 0.3 3.3 null null 3 2016-05-06T17:01:51.000Z 2016-05-06T17:02:17.000Z 1.0 0.0 5.0 N 226 226 2 30.0 0.0 0.5 0.0 0.0 0.3 30.8 null null 3 2016-05-06T17:02:57.000Z 2016-05-06T17:03:41.000Z 1.0 0.0 1.0 N 226 226 2 2.5 1.0 0.5 0.0 0.0 0.3 4.3 null null 3 2016-05-06T18:32:01.000Z 2016-05-06T18:39:37.000Z 1.0 0.9 1.0 N 229 161 2 6.5 1.0 0.5 0.0 0.0 0.3 8.3 null null 3 2016-05-06T18:41:14.000Z 2016-05-06T19:00:58.000Z 1.0 2.13 1.0 N 161 107 1 13.5 1.0 0.5 2.5 0.0 0.3 17.8 null null 3 2016-05-06T19:03:40.000Z 2016-05-06T19:19:27.000Z 1.0 0.91 1.0 N 107 234 1 10.5 1.0 0.5 1.0 0.0 0.3 13.3 null null 3 2016-05-06T19:22:48.000Z 2016-05-06T19:31:21.000Z 1.0 1.43 1.0 N 234 170 1 7.5 1.0 0.5 2.0 0.0 0.3 11.3 null null 3 2016-05-06T19:34:28.000Z 2016-05-06T20:00:18.000Z 1.0 1.97 1.0 N 162 48 2 16.0 1.0 0.5 0.0 0.0 0.3 17.8 null null 3 2016-05-06T20:05:34.000Z 2016-05-06T20:30:46.000Z 1.0 10.21 1.0 N 138 48 1 30.5 0.5 0.5 5.0 5.54 0.3 42.34 null null 3 2016-05-06T20:50:30.000Z 2016-05-06T20:55:23.000Z 1.0 0.71 1.0 N 164 186 1 5.0 0.5 0.5 1.0 0.0 0.3 7.3 null null 3 2016-05-06T20:59:46.000Z 2016-05-06T21:20:26.000Z 1.0 2.28 1.0 N 90 148 2 14.0 0.5 0.5 0.0 0.0 0.3 15.3 null null 3 2016-05-06T20:12:51.000Z 2016-05-06T20:12:52.000Z 1.0 0.0 1.0 N 207 207 1 2.5 0.5 0.5 0.0 0.0 0.3 3.8 null null 3 2016-05-06T20:06:21.000Z 2016-05-06T20:15:45.000Z 1.0 1.12 1.0 N 100 137 2 7.5 0.5 0.5 0.0 0.0 0.3 8.8 null null 3 2016-05-06T20:49:04.000Z 2016-05-06T21:02:17.000Z 1.0 1.14 1.0 N 234 224 1 9.0 0.5 0.5 1.0 0.0 0.3 11.3 null null 3 2016-05-06T21:26:06.000Z 2016-05-06T21:28:34.000Z 1.0

In [0]:
%sql
SELECT MAX(total_amount), MIN(total_amount)
FROM df_yellow

MAX(total_amount) MIN(total_amount) 1.0000015E7 -2567.8

In [0]:
%sql
SELECT COUNT(*)
FROM df_yellow
WHERE total_amount <= 0 OR total_amount > 500

COUNT(*) 2001455

In [0]:
%sql
--total amount
SELECT COUNT(*)
FROM df_green
WHERE total_amount <= 0 AND payment_type = 6

COUNT(*) 0

In [0]:
%sql 

CREATE OR REPLACE TEMPORARY VIEW df_yellow_cleaned AS
WITH 
p AS (
  SELECT
    TIMESTAMP('2009-01-01 00:00:00') AS min_date,
    TIMESTAMP('2024-12-31 23:59:59') AS max_date,
    1.0 AS min_speed,
    70.0 AS max_speed,
    1.0 AS min_duration,
    120.0 AS max_duration,
    0.2 AS min_distance,
    100.0 AS max_distance,
    5 AS passenger_cap
),

base AS (
  SELECT 
    'yellow' AS color,
    VendorID AS VendorID_raw,
    tpep_pickup_datetime AS pickup_dt,
    tpep_dropoff_datetime AS dropoff_dt,
    store_and_fwd_flag AS store_and_fwd_flag,
    CAST(trip_distance AS double) AS trip_distance,
    CAST(passenger_count AS int) AS passenger_raw,
    
    RatecodeID AS RatecodeID_raw,
    PULocationID AS PULocationID,
    DOLocationID AS DOLocationID,
    fare_amount AS fare_amount,
    extra AS extra,
    mta_tax AS mta_tax,
    tip_amount AS tip_amount,
    tolls_amount AS tolls_amount,
    improvement_surcharge AS improvement_surcharge,
    congestion_surcharge AS congestion_surcharge,
    airport_fee AS airport_fee,
    CAST(total_amount AS double) AS total_amount,
    CAST(payment_type AS int) payment_type_raw
  FROM df_yellow
),

derived AS(
  SELECT * EXCEPT (passenger_raw, RatecodeID_raw, VendorID_raw, payment_type_raw),
    (unix_timestamp(dropoff_dt) - unix_timestamp(pickup_dt))/60 AS trip_duration_min,
    (unix_timestamp(dropoff_dt) - unix_timestamp(pickup_dt))/3600 AS trip_duration_hr,
    CASE 
      WHEN passenger_raw IS NULL THEN NULL
      WHEN passenger_raw < 0 THEN NULL
      WHEN passenger_raw = 0 THEN 1
      WHEN passenger_raw > (SELECT passenger_cap FROM p) THEN (SELECT passenger_cap FROM p)
      ELSE passenger_raw
    END AS passenger_count,
    CASE
      WHEN RatecodeID_raw IS NULL THEN 99
      ELSE RatecodeID_raw
    END AS RatecodeID,
    CASE
      WHEN VendorID_raw NOT IN (1, 2, 6, 7) THEN NULL
      ELSE VendorID_raw
    END AS VendorID,
    CASE
      WHEN payment_type_raw IS NULL THEN 5
      ELSE payment_type_raw
    END AS payment_type
  FROM base
)

SELECT * EXCEPT (trip_duration_min, trip_duration_hr)
FROM derived
WHERE 
  dropoff_dt > pickup_dt
  AND pickup_dt BETWEEN (SELECT min_date FROM p) AND (SELECT max_date FROM p)
  AND dropoff_dt BETWEEN (SELECT min_date FROM p) AND (SELECT max_date FROM p)

  AND trip_duration_min BETWEEN (SELECT min_duration FROM p) AND (SELECT max_duration FROM p)
  
  AND trip_distance <= (SELECT max_distance FROM p)
  AND trip_distance > (SELECT min_distance FROM p)

  AND (trip_distance/ NULLIF(trip_duration_hr,0) ) BETWEEN (SELECT min_speed FROM p) AND (SELECT max_speed FROM p)

  AND total_amount IS NOT NULL
  AND total_amount > 0
   AND total_amount <= 200

  AND PULocationID IS NOT NULL
  AND DOLocationID IS NOT NULL
;

In [0]:
%sql
--Count of yellow records before and after cleaned, cleaned ratio
SELECT 
  raw_count,
  cleaned_count,
  cleaned_count / raw_count AS ratio
FROM (
  SELECT 
    (SELECT COUNT(*) FROM df_yellow) AS raw_count,
    (SELECT COUNT(*) FROM df_yellow_cleaned) AS cleaned_count
)

raw_count cleaned_count ratio 907982776 889880080 0.9800627319388711

In [0]:
%sql
SELECT * FROM df_yellow_cleaned LIMIT 10

color pickup_dt dropoff_dt store_and_fwd_flag trip_distance PULocationID DOLocationID fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge congestion_surcharge airport_fee total_amount passenger_count RatecodeID VendorID payment_type yellow 2015-01-01T00:11:33.000Z 2015-01-01T00:16:48.000Z N 1.0 41 166 5.7 0.5 0.5 1.4 0.0 0.0 null null 8.4 1 1.0 1 1 yellow 2015-01-01T00:18:24.000Z 2015-01-01T00:24:20.000Z N 0.9 166 238 6.0 0.5 0.5 0.0 0.0 0.0 null null 7.3 1 1.0 1 3 yellow 2015-01-01T00:26:19.000Z 2015-01-01T00:41:06.000Z N 3.5 238 162 13.2 0.5 0.5 2.9 0.0 0.0 null null 17.4 1 1.0 1 1 yellow 2015-01-01T00:45:26.000Z 2015-01-01T00:53:20.000Z N 2.1 162 263 8.2 0.5 0.5 2.37 0.0 0.0 null null 11.87 1 1.0 1 1 yellow 2015-01-01T00:59:21.000Z 2015-01-01T01:05:24.000Z N 1.0 236 141 6.0 0.5 0.5 0.0 0.0 0.0 null null 7.3 1 1.0 1 3 yellow 2015-01-01T00:07:31.000Z 2015-01-01T00:11:32.000Z N 0.8 239 238 5.0 0.5 0.5 0.0 0.0 0.0 null null 6.3 1 1.0 1 2 yellow 2015-01-01T00:47:08.000Z 2015-01-01T00:54:50.000Z N 1.1 238 239 7.0 0.5 0.5 0.0 0.0 0.0 null null 8.3 1 1.0 1 2 yellow 2015-01-01T00:58:04.000Z 2015-01-01T01:11:56.000Z N 2.9 238 42 12.2 0.5 0.5 2.7 0.0 0.0 null null 16.2 1 1.0 1 1 yellow 2015-01-01T00:29:25.000Z 2015-01-01T00:37:25.000Z N 1.3 90 125 7.0 0.5 0.5 0.0 0.0 0.0 null null 8.3 2 1.0 1 2 yellow 2015-01-01T00:39:02.000Z 2015-01-01T01:02:37.000Z N 4.3 125 141 18.0 0.5 0.5 0.0 0.0 0.0 null null 19.3 2 1.0 1 2

## 1.5. Count green and yellow records after cleaned

In [0]:
%sql
SELECT green_cleaned_count, yellow_cleaned_count
FROM (
  SELECT
    (SELECT COUNT(*) FROM df_green_cleaned) AS green_cleaned_count,
    (SELECT COUNT(*) FROM df_yellow_cleaned) AS yellow_cleaned_count
)

green_cleaned_count yellow_cleaned_count 80458710 889880080

## 1.6. Combine green and yellow records

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW df_green_yellow AS
SELECT color,
      VendorID,
      RatecodeID,
      pickup_dt,
      dropoff_dt,
      store_and_fwd_flag,
      trip_distance,
      passenger_count,
      PULocationID,
      DOLocationID,
      payment_type,
      total_amount,
      extra,
      mta_tax,
      tip_amount,
      improvement_surcharge,
      congestion_surcharge,
      trip_type
FROM df_green_cleaned 

UNION ALL 

SELECT color,
      VendorID,
      RatecodeID,
      pickup_dt,
      dropoff_dt,
      store_and_fwd_flag,
      trip_distance,
      passenger_count,
      PULocationID,
      DOLocationID,
      payment_type,
      total_amount,
      extra,
      mta_tax,
      tip_amount,
      improvement_surcharge,
      congestion_surcharge,
      1 AS trip_type
FROM df_yellow_cleaned;

In [0]:
%sql
SELECT COUNT(*) FROM df_green_yellow

COUNT(*) 970338790

## 1.7. Combine with location data

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW df_join_all AS
SELECT 
  gy.*,
  pu.Borough AS PU_Borough,
  pu.Zone AS PU_Zone,
  pu.service_zone AS PU_service_zone,
  dr.Borough AS DR_Borough,
  dr.Zone AS DR_Zone,
  dr.service_zone AS DR_service_zone
FROM df_green_yellow gy
LEFT JOIN df_lookup pu ON gy.PULocationID = pu.LocationID
LEFT JOIN df_lookup dr ON gy.DOLocationID = dr.LocationID

In [0]:
%sql
SELECT COUNT(*) FROM df_join_all

COUNT(*) 970338790

## 1.8. Save as table

In [0]:
%sql
CREATE OR REPLACE TABLE bde.final_trips_cleaned
USING DELTA
AS
SELECT * FROM df_join_all

## 1.9. Final table count

In [0]:
%sql
SELECT COUNT(*) AS final_row_count
FROM bde.final_trips_cleaned;

final_row_count 970457848